<a href="https://colab.research.google.com/github/rohansiddam/Python-Journey/blob/main/025%20-%20Lesson%2025%20(Meteorite%20Landings%20-%20Cartograms).ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Lesson 25: Meteorite Landings - Cartograms

### Teacher-Student Activities

In the previous classes, we learnt how to remove the unwanted data points from a data set and how to treat the missing values. We also learnt how to create a simple map (or a cartogram) using the `folium` module. In this class, we will continue from where we left off two classes back, i.e., we will continue from the part where we learnt how to treat the missing values. There we replaced the missing year values with the median year value.

Now, we need to create cartograms for the meteorite landing sites. Essentially, we want to create a world map having markers for the location from where a meteorite was found. Since there are over 30,000 meteorites, plotting the markers for all of them in a single cartogram will become too cluttered to make any kind of interpretation. Hence, we will create cartograms for the 5 year period at a time. For e.g., we will create different cartograms for 2001 to 2005 period, 2006 to 2010 period, 2011 to 2015 period etc.

Let's quickly run the codes that we have already covered in the previous classes and begin this class from **Activity 1: Converting The `year` Values To `int`** section. You too run the codes until the first activity.




---

#### The Data

The dataset contains the following variables:

1. `name`: the name of the place where a meteorite was found or observed.

2. `id`: a unique identifier for a meteorite.

3. `nametype`: one of the following:
    
    - `valid`: a typical meteorite.
    
    - `relict`: a meteorite that has been highly degraded by the weather on Earth.

4. `recclass`: the class of the meteorite; one of a large number of classes based on physical, chemical, and other characteristics.

5. `mass:` the mass of the meteorite, in grams

6. `fall`: whether the meteorite was seen falling, or was discovered after its impact; one of the following:

    - `Fell`: the meteorite's fall was observed.
    
    - `Found`: the meteorite's fall was not observed.

7. `year`: the year the meteorite fell, or the year it was found (depending on the value of fell).

8. `reclat`: the latitude of the meteorite's landing.

9. `reclong`: the longitude of the meteorite's landing.

10. `GeoLocation`: a parentheses-enclose, comma-separated tuple that combines `reclat` and `reclong` values.


---

#### Loading The Dataset

Dataset Link (don't click on them):

https://student-datasets-bucket.s3.ap-south-1.amazonaws.com/whitehat-ds-datasets/meteorite-landings/meteorite-landings.csv


In [ ]:
# Import the 'numpy', 'pandas' and 'matplotlib.pyplot' libraries for this class and create a DataFrame.
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt

met_df = pd.read_csv('https://student-datasets-bucket.s3.ap-south-1.amazonaws.com/whitehat-ds-datasets/meteorite-landings/meteorite-landings.csv')
met_df.head()

name   id nametype     recclass      mass  fall    year    reclat  \
0    Aachen    1    Valid           L5      21.0  Fell  1880.0  50.77500   
1    Aarhus    2    Valid           H6     720.0  Fell  1951.0  56.18333   
2      Abee    6    Valid          EH4  107000.0  Fell  1952.0  54.21667   
3  Acapulco   10    Valid  Acapulcoite    1914.0  Fell  1976.0  16.88333   
4   Achiras  370    Valid           L6     780.0  Fell  1902.0 -33.16667   

     reclong               GeoLocation  
0    6.08333     (50.775000, 6.083330)  
1   10.23333    (56.183330, 10.233330)  
2 -113.00000  (54.216670, -113.000000)  
3  -99.90000   (16.883330, -99.900000)  
4  -64.95000  (-33.166670, -64.950000)

In [ ]:
# Number of rows and columns in the DataFrame.
met_df.shape

(45716, 10)

---

In [ ]:
# Descriptive statistics for the 'year' values in the 'met_df' DataFrame.
met_df['year'].describe()

count    45428.000000
mean      1991.772189
std         27.181247
min        301.000000
25%       1987.000000
50%       1998.000000
75%       2003.000000
max       2501.000000
Name: year, dtype: float64

---

#### Slicing A Dataframe And The Ampersand (`&`) Logical Operator

**Syntax:** `data_frame[condition1 & condition2 & condition3 ... conditionN]`

where `N` is the total number of conditions to be applied.


In [ ]:
# Rows containing the year values less than 860 and greater than 2016.
correct_years_df = met_df[(met_df['year'] >= 860) & (met_df['year'] <= 2016)]
correct_years_df

name     id nametype              recclass      mass   fall  \
0          Aachen      1    Valid                    L5      21.0   Fell   
1          Aarhus      2    Valid                    H6     720.0   Fell   
2            Abee      6    Valid                   EH4  107000.0   Fell   
3        Acapulco     10    Valid           Acapulcoite    1914.0   Fell   
4         Achiras    370    Valid                    L6     780.0   Fell   
...           ...    ...      ...                   ...       ...    ...   
45711  Zillah 002  31356    Valid               Eucrite     172.0  Found   
45712      Zinder  30409    Valid  Pallasite, ungrouped      46.0  Found   
45713        Zlin  30410    Valid                    H4       3.3  Found   
45714   Zubkovsky  31357    Valid                    L6    2167.0  Found   
45715  Zulu Queen  30414    Valid                  L3.7     200.0  Found   

         year    reclat    reclong               GeoLocation  
0      1880.0  50.77500    6.08333     (50.775000, 6.083330)  
1      1951.0  56.18333   10.23333    (56.183330, 10.233330)  
2      1952.0  54.21667 -113.00000  (54.216670, -113.000000)  
3      1976.0  16.88333  -99.90000   (16.883330, -99.900000)  
4      1902.0 -33.16667  -64.95000  (-33.166670, -64.950000)  
...       ...       ...        ...                       ...  
45711  1990.0  29.03700   17.01850    (29.037000, 17.018500)  
45712  1999.0  13.78333    8.96667     (13.783330, 8.966670)  
45713  1939.0  49.25000   17.66667    (49.250000, 17.666670)  
45714  2003.0  49.78917   41.50460    (49.789170, 41.504600)  
45715  1976.0  33.98333 -115.68333  (33.983330, -115.683330)  

[45424 rows x 10 columns]

---

#### Removing The Invalid `reclong` Values


In [ ]:
# Rows having the 'reclong' values greater than or equal to -180 degrees and less than or equal to 180 degrees.
correct_long_df = correct_years_df[(correct_years_df['reclong'] >= -180) & (correct_years_df['reclong'] <= 180)]
correct_long_df

name     id nametype              recclass      mass   fall  \
0          Aachen      1    Valid                    L5      21.0   Fell   
1          Aarhus      2    Valid                    H6     720.0   Fell   
2            Abee      6    Valid                   EH4  107000.0   Fell   
3        Acapulco     10    Valid           Acapulcoite    1914.0   Fell   
4         Achiras    370    Valid                    L6     780.0   Fell   
...           ...    ...      ...                   ...       ...    ...   
45711  Zillah 002  31356    Valid               Eucrite     172.0  Found   
45712      Zinder  30409    Valid  Pallasite, ungrouped      46.0  Found   
45713        Zlin  30410    Valid                    H4       3.3  Found   
45714   Zubkovsky  31357    Valid                    L6    2167.0  Found   
45715  Zulu Queen  30414    Valid                  L3.7     200.0  Found   

         year    reclat    reclong               GeoLocation  
0      1880.0  50.77500    6.08333     (50.775000, 6.083330)  
1      1951.0  56.18333   10.23333    (56.183330, 10.233330)  
2      1952.0  54.21667 -113.00000  (54.216670, -113.000000)  
3      1976.0  16.88333  -99.90000   (16.883330, -99.900000)  
4      1902.0 -33.16667  -64.95000  (-33.166670, -64.950000)  
...       ...       ...        ...                       ...  
45711  1990.0  29.03700   17.01850    (29.037000, 17.018500)  
45712  1999.0  13.78333    8.96667     (13.783330, 8.966670)  
45713  1939.0  49.25000   17.66667    (49.250000, 17.666670)  
45714  2003.0  49.78917   41.50460    (49.789170, 41.504600)  
45715  1976.0  33.98333 -115.68333  (33.983330, -115.683330)  

[38221 rows x 10 columns]

---

#### Removing The Rows Containing `0 N, 0 E` Values


In [ ]:
# Rows containing the 0 'reclat' and 0 'reclong' values from the 'correct_long_df'.
correct_lat_long_df = correct_long_df[~((correct_long_df['reclat'] == 0) & (correct_long_df['reclong'] == 0))]
correct_lat_long_df

name     id nametype              recclass      mass   fall  \
0          Aachen      1    Valid                    L5      21.0   Fell   
1          Aarhus      2    Valid                    H6     720.0   Fell   
2            Abee      6    Valid                   EH4  107000.0   Fell   
3        Acapulco     10    Valid           Acapulcoite    1914.0   Fell   
4         Achiras    370    Valid                    L6     780.0   Fell   
...           ...    ...      ...                   ...       ...    ...   
45711  Zillah 002  31356    Valid               Eucrite     172.0  Found   
45712      Zinder  30409    Valid  Pallasite, ungrouped      46.0  Found   
45713        Zlin  30410    Valid                    H4       3.3  Found   
45714   Zubkovsky  31357    Valid                    L6    2167.0  Found   
45715  Zulu Queen  30414    Valid                  L3.7     200.0  Found   

         year    reclat    reclong               GeoLocation  
0      1880.0  50.77500    6.08333     (50.775000, 6.083330)  
1      1951.0  56.18333   10.23333    (56.183330, 10.233330)  
2      1952.0  54.21667 -113.00000  (54.216670, -113.000000)  
3      1976.0  16.88333  -99.90000   (16.883330, -99.900000)  
4      1902.0 -33.16667  -64.95000  (-33.166670, -64.950000)  
...       ...       ...        ...                       ...  
45711  1990.0  29.03700   17.01850    (29.037000, 17.018500)  
45712  1999.0  13.78333    8.96667     (13.783330, 8.966670)  
45713  1939.0  49.25000   17.66667    (49.250000, 17.666670)  
45714  2003.0  49.78917   41.50460    (49.789170, 41.504600)  
45715  1976.0  33.98333 -115.68333  (33.983330, -115.683330)  

[32036 rows x 10 columns]

---

#### Check For The Missing Values



In [ ]:
# Check whether the 'correct_lat_long_df' DataFrame has missing values or not.
correct_lat_long_df.isnull().sum()

name             0
id               0
nametype         0
recclass         0
mass           107
fall             0
year             0
reclat           0
reclong          0
GeoLocation      0
dtype: int64

In [ ]:
# Rows containing the missing 'mass' values in the 'correct_lat_long_df' DataFrame.
correct_lat_long_df[correct_lat_long_df['mass'].isnull() == True]

name     id nametype      recclass  mass   fall    year  \
12       Aire-sur-la-Lys    425    Valid       Unknown   NaN   Fell  1769.0   
38                Angers   2301    Valid            L6   NaN   Fell  1822.0   
76     Barcelona (stone)   4944    Valid            OC   NaN   Fell  1704.0   
93              Belville   5009    Valid            OC   NaN   Fell  1937.0   
172    Castel Berardenga   5292    Valid    Stone-uncl   NaN   Fell  1791.0   
...                  ...    ...      ...           ...   ...    ...     ...   
31097            Palermo  18076    Valid       Unknown   NaN  Found  1966.0   
36812           San Luis  23129    Valid             H   NaN  Found  1964.0   
38278            Weiyuan  24233    Valid  Mesosiderite   NaN  Found  1978.0   
41460      Yamato 792768  28117    Valid           CM2   NaN  Found  1979.0   
45698      Zapata County  30393    Valid          Iron   NaN  Found  1930.0   

         reclat    reclong               GeoLocation  
12     50.66667    2.33333     (50.666670, 2.333330)  
38     47.46667   -0.55000    (47.466670, -0.550000)  
76     41.36667    2.16667     (41.366670, 2.166670)  
93    -32.33333  -64.86667  (-32.333330, -64.866670)  
172    43.35000   11.50000    (43.350000, 11.500000)  
...         ...        ...                       ...  
31097 -34.55000  -58.43333  (-34.550000, -58.433330)  
36812 -33.33333  -66.38333  (-33.333330, -66.383330)  
38278  35.26667  104.31667   (35.266670, 104.316670)  
41460 -71.50000   35.66667   (-71.500000, 35.666670)  
45698  27.00000  -99.00000   (27.000000, -99.000000)  

[107 rows x 10 columns]

In [ ]:
# Descriptive statistics for the 'mass' column in the 'correct_lat_long_df' DataFrame.
correct_lat_long_df['mass'].describe()

count    3.192900e+04
mean     1.854289e+04
std      6.868495e+05
min      0.000000e+00
25%      6.500000e+00
50%      2.960000e+01
75%      2.020000e+02
max      6.000000e+07
Name: mass, dtype: float64

The median `mass` value is 29.6 grams. After replacing the `NaN` values with the median value all the above rows in the `mass` column should have `29.6` value.

---

#### The `index` Keyword


In [ ]:
# List of the indices of above rows.
row_indices = correct_lat_long_df[correct_lat_long_df['mass'].isnull() == True].index
row_indices

Int64Index([   12,    38,    76,    93,   172,   204,   262,   308,   312,
              320,
            ...
            31055, 31056, 31057, 31058, 31059, 31097, 36812, 38278, 41460,
            45698],
           dtype='int64', length=107)

So, here we have an array containing the indices of all the rows having the `NaN` mass values. There are 107 such rows.

---

#### The `loc[]` Function


In [ ]:
# Missing 'mass' values from 'correct_lat_long_df' DataFrame using the 'loc[]' function.
missing_mass_values = correct_lat_long_df.loc[row_indices, 'mass']
missing_mass_values

12      NaN
38      NaN
76      NaN
93      NaN
172     NaN
         ..
31097   NaN
36812   NaN
38278   NaN
41460   NaN
45698   NaN
Name: mass, Length: 107, dtype: float64

Here, we have a Pandas series which contains all the `NaN` mass values. The length of this series is `107`.

---

#### Replacing The Missing `mass` Values

**Note:** The code below will throw a warning. Ignore it!


In [ ]:
# Missing values in the 'mass' column in the 'correct_lat_long_df' DataFrame with median of mass.
correct_lat_long_df.loc[row_indices, 'mass'] = correct_lat_long_df['mass'].median()

/usr/local/lib/python3.7/dist-packages/pandas/core/indexing.py:1817: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_single_column(loc, value, pi)


In [ ]:
# Check whether all the missing mass values have been replaced by the median of the mass values or not.
correct_lat_long_df.loc[row_indices, :]

name     id nametype      recclass  mass   fall    year  \
12       Aire-sur-la-Lys    425    Valid       Unknown  29.6   Fell  1769.0   
38                Angers   2301    Valid            L6  29.6   Fell  1822.0   
76     Barcelona (stone)   4944    Valid            OC  29.6   Fell  1704.0   
93              Belville   5009    Valid            OC  29.6   Fell  1937.0   
172    Castel Berardenga   5292    Valid    Stone-uncl  29.6   Fell  1791.0   
...                  ...    ...      ...           ...   ...    ...     ...   
31097            Palermo  18076    Valid       Unknown  29.6  Found  1966.0   
36812           San Luis  23129    Valid             H  29.6  Found  1964.0   
38278            Weiyuan  24233    Valid  Mesosiderite  29.6  Found  1978.0   
41460      Yamato 792768  28117    Valid           CM2  29.6  Found  1979.0   
45698      Zapata County  30393    Valid          Iron  29.6  Found  1930.0   

         reclat    reclong               GeoLocation  
12     50.66667    2.33333     (50.666670, 2.333330)  
38     47.46667   -0.55000    (47.466670, -0.550000)  
76     41.36667    2.16667     (41.366670, 2.166670)  
93    -32.33333  -64.86667  (-32.333330, -64.866670)  
172    43.35000   11.50000    (43.350000, 11.500000)  
...         ...        ...                       ...  
31097 -34.55000  -58.43333  (-34.550000, -58.433330)  
36812 -33.33333  -66.38333  (-33.333330, -66.383330)  
38278  35.26667  104.31667   (35.266670, 104.316670)  
41460 -71.50000   35.66667   (-71.500000, 35.666670)  
45698  27.00000  -99.00000   (27.000000, -99.000000)  

[107 rows x 10 columns]

In [ ]:
# Descriptive statistics for the 'mass' column in the above DataFrame containing 107 rows.
correct_lat_long_df.loc[row_indices, 'mass'].describe()

count    107.0
mean      29.6
std        0.0
min       29.6
25%       29.6
50%       29.6
75%       29.6
max       29.6
Name: mass, dtype: float64

In [ ]:
# Descriptive statistics for the 'mass' column in the 'correct_lat_long_df' DataFrame.
correct_lat_long_df['mass'].describe()

count    3.203600e+04
mean     1.848105e+04
std      6.857023e+05
min      0.000000e+00
25%      6.500000e+00
50%      2.960000e+01
75%      2.006500e+02
max      6.000000e+07
Name: mass, dtype: float64

---

#### Activity 1: Converting The `year` Values To `int`

Now that we have replaced the missing `mass` values with the `median` value, let's convert the `year` values into integer type values because currently they are floating-point values. The `year` values as the floating-point type doesn't make sense because a year is always a whole number.

To convert values in a Pandas series to another data-type, we use the `astype()` function. It takes the target data-type as an input and returns the values in the series in the desired data type.

**Note:** The code below will throw a warning. Ignore it!


In [ ]:
# Student Action: Convert the 'year' values into integer type values.
correct_lat_long_df['year'] = correct_lat_long_df['year'].astype(int)

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  


Now, let's confirm whether we have converted the `year` values into integer using the `dtype` keyword. We learnt about the `dtype` keyword in the NumPy arrays class.

In [ ]:
# Student Action: Confirm whether the 'year' values are integer or not using the 'dtype' keyword.
correct_lat_long_df['year'].dtype

dtype('int64')

---

#### Activity 2: The Good & Withered Meteorites Separation

Our next task is to make a cartogram for the landing locations of the meteorites found on Earth. They were found in two conditions: the good and the withered condition. The condition of the meteorites is described in the `nametype` column. If the `nametype` value is `Valid`, then it means the condition of the meteorite found is good whereas if the `nametype` value is `Relict`, then it means the condition of the meteorite found is withered.

Before creating a cartogram, let's create two DataFrames.

- The first DataFrame for the meteorites which were actually found and are in good condition (`nametype` value is `Valid`).

- The second DataFrame for the meteorites which were actually found and are in a withered condition (`nametype` value is `Relict`).

In [ ]:
# Student Action: Find out how many meteorites are in good condition ('nametype' == 'Valid') and how many are withered ('nametype' == 'Relict').
correct_lat_long_df['nametype'].value_counts()

Valid     31967
Relict       69
Name: nametype, dtype: int64

In [ ]:
correct_lat_long_df.head()

name   id nametype     recclass      mass  fall  year    reclat  \
0    Aachen    1    Valid           L5      21.0  Fell  1880  50.77500   
1    Aarhus    2    Valid           H6     720.0  Fell  1951  56.18333   
2      Abee    6    Valid          EH4  107000.0  Fell  1952  54.21667   
3  Acapulco   10    Valid  Acapulcoite    1914.0  Fell  1976  16.88333   
4   Achiras  370    Valid           L6     780.0  Fell  1902 -33.16667   

     reclong               GeoLocation  
0    6.08333     (50.775000, 6.083330)  
1   10.23333    (56.183330, 10.233330)  
2 -113.00000  (54.216670, -113.000000)  
3  -99.90000   (16.883330, -99.900000)  
4  -64.95000  (-33.166670, -64.950000)

So, there are only 69 meteorites which have withered due to the prolonged exposure to probably the extreme weather conditions. The other meteorites are in good condition. Since the withered meteorites are fewer in numbers, let's create a DataFrame for the same and create its cartogram because it would be easier for us to spot these meteorites on a map.

In [ ]:
# Student Action: Create a DataFrame called 'found_relict_df' and store data only for those meteorites which were actually found.
found_relict_df = correct_lat_long_df[ (correct_lat_long_df['fall'] == 'Found') & (correct_lat_long_df['nametype'] == 'Relict') ]
found_relict_df

name     id nametype                recclass  mass  \
5182               Brunflo   5157   Relict                Relict H  29.6   
6810   David Glacier 92308   6614   Relict  Chondrite-fusion crust   1.7   
12627                 Gove  52859   Relict             Relict iron   0.0   
15944        Gullhögen 001  44889   Relict               Relict OC  29.6   
20674    Lewis Cliff 87241  13702   Relict  Chondrite-fusion crust   0.5   
...                    ...    ...      ...                     ...   ...   
31072       Österplana 060  56159   Relict               Relict OC   0.0   
31073       Österplana 061  56160   Relict               Relict OC   0.0   
31074       Österplana 062  56161   Relict               Relict OC   0.0   
31075       Österplana 063  56162   Relict               Relict OC   0.0   
31076       Österplana 064  56163   Relict               Relict OC   0.0   

        fall  year    reclat    reclong               GeoLocation  
5182   Found  1980  63.11667   14.28333    (63.116670, 14.283330)  
6810   Found  1992 -75.31667  162.00000  (-75.316670, 162.000000)  
12627  Found  1979 -12.26333  136.83833  (-12.263330, 136.838330)  
15944  Found  2000  58.38333   13.80000    (58.383330, 13.800000)  
20674  Found  1987 -84.34563  161.31058  (-84.345630, 161.310580)  
...      ...   ...       ...        ...                       ...  
31072  Found  2009  58.58333   13.43333    (58.583330, 13.433330)  
31073  Found  2009  58.58333   13.43333    (58.583330, 13.433330)  
31074  Found  2010  58.58333   13.43333    (58.583330, 13.433330)  
31075  Found  2010  58.58333   13.43333    (58.583330, 13.433330)  
31076  Found  2011  58.58333   13.43333    (58.583330, 13.433330)  

[69 rows x 10 columns]

Now, create a DataFrame for the meteorites which were actually found and are in good condition (`nametype` value is `Valid`).

In [ ]:
# Student Action: Create a DataFrame called 'found_valid_df' and store data only for those meteorites which were actually found.
found_valid_df = correct_lat_long_df[ (correct_lat_long_df['fall'] == 'Found') & (correct_lat_long_df['nametype'] == 'Valid')]
found_valid_df

name     id nametype              recclass      mass   fall  \
1108             Abajo      4    Valid                    H5    331.00  Found   
1109   Abar al' Uj 001  51399    Valid                  H3.8    194.34  Found   
1110            Abbott      5    Valid                  H3-6  21100.00  Found   
1111         Abernathy      7    Valid                    L6   2914.00  Found   
1112               Abo      8    Valid                     H      1.20  Found   
...                ...    ...      ...                   ...       ...    ...   
45711       Zillah 002  31356    Valid               Eucrite    172.00  Found   
45712           Zinder  30409    Valid  Pallasite, ungrouped     46.00  Found   
45713             Zlin  30410    Valid                    H4      3.30  Found   
45714        Zubkovsky  31357    Valid                    L6   2167.00  Found   
45715       Zulu Queen  30414    Valid                  L3.7    200.00  Found   

       year    reclat    reclong               GeoLocation  
1108   1982  26.80000 -105.41667  (26.800000, -105.416670)  
1109   2008  22.72192   48.95937    (22.721920, 48.959370)  
1110   1951  36.30000 -104.28333  (36.300000, -104.283330)  
1111   1941  33.85000 -101.80000  (33.850000, -101.800000)  
1112   1840  60.43333   22.30000    (60.433330, 22.300000)  
...     ...       ...        ...                       ...  
45711  1990  29.03700   17.01850    (29.037000, 17.018500)  
45712  1999  13.78333    8.96667     (13.783330, 8.966670)  
45713  1939  49.25000   17.66667    (49.250000, 17.666670)  
45714  2003  49.78917   41.50460    (49.789170, 41.504600)  
45715  1976  33.98333 -115.68333  (33.983330, -115.683330)  

[30871 rows x 10 columns]

So there are 30,871 meteorites which were found in good condition.

---

#### Activity 3: Cartogram For Withered Meteorites^

Let's create a cartogram for all the withered meteorites that were found. We need to add a marker for every single meteorite listed in the `found_relict_df`. Hence, we need to use the `for` loop to iterate through each entry in the `found_reliect_df` DataFrame. Then we also need to use the `loc[]` function to get the latitude and longitude values for each meteorite. Since we need to display the location of the meteorite site in each marker through the popup window, we again will have to use the `loc[]` function.

**Note:** If you are creating a world map, then provide the coordinates of the equator (`0, 0`) as input in the `Map()` function to create a symmetric map.

In [ ]:
# Teacher Action: Create a cartogram for the landing sites of the meteorites found in the withered condition.
import folium
map1 = folium.Map(location = [0,0], width = '90%', tiles = 'OpenStreetMap', zoom_start = 2)
for i in found_relict_df.index:
  folium.Marker(location = [found_relict_df.loc[i,'reclat'], found_relict_df.loc[i, 'reclong']], popup = found_relict_df.loc[i, 'name']).add_to(map1)


In [ ]:
map1

In the above code:

1. We created a world map by providing the coordinates of the equator as an input to the `Map()` function with the `zoom_start` value equal to 1. For a better visibility, we have chosen the `Stamen Toner` background for the map.

2. Next, we are adding the markers to the map for each meteorite existing in the `found_relict_df` DataFrame using the `for` loop.

    - The `for` loop iterates through each index in the `found_relict_df` DataFrame. Recall that to get the array containing the indices for a Pandas series, we use the `index` keyword.

    ```
    for i in found_relict_df.index:
    ```

    - Using the `loc[]` function, we get the `reclat`, `reclong` and `name` values from the `found_relict_df` DataFrame.

    ```
    for i in found_relict_df.index:
        folium.Marker(location=[found_relict_df.loc[i, 'reclat'], found_relict_df.loc[i, 'reclong']],
                popup=found_relict_df.loc[i, 'name']).add_to(map1)
    ```

    - The `add_to()` function adds a marker to the `map1` map for each meteorite existing in the `found_relict_df` DataFrame.




In [ ]:
found_valid_df[found_valid_df['year'] > 2010].shape

(398, 10)

---

#### Activity 4: Cartograms For Good Condition Meteorites^^^

Now, let's make a cartogram for the meteorites which are found in good condition (`found_valid_df`). As we saw earlier, 30,871 meteorites were found in good condition. Hence, creating markers for each of these meteorites is impractical. So, we can slice the `found_valid_df` DataFrame based on year.

Let's estimate how many meteorites were found in good condition after the year 2010.

In [ ]:
# Student Action: Find out how many meteorites were found in good condition after the year 2010.
found_valid_df['year'].value_counts()

1979    3043
1988    2289
2003    1704
1999    1571
1997    1502
        ... 
1865       1
1819       1
1575       1
1793       1
1792       1
Name: year, Length: 199, dtype: int64

So, 398 meteorites were found in good condition after the year 2010. Let's create a cartogram for these meteorites. We will use the same process which we used to create a cartogram for the withered meteorites.



In [ ]:
# Student Action: Create a cartogram for the meteorites found in good condition after the year 2010. Popup the location name.
map2 = folium.Map(location = [0,0], width = '90%', tiles = 'OpenStreetMap', zoom_start = 2)
for i in found_valid_df[found_valid_df['year'] > 2010].index:
  folium.Marker(location = [found_valid_df[found_valid_df['year'] > 2010].loc[i,'reclat'], found_valid_df[found_valid_df['year'] > 2010].loc[i, 'reclong']], popup = found_valid_df[found_valid_df['year'] > 2010].loc[i, 'name']).add_to(map2)

In [ ]:
map2

Similarly, let's create a cartogram for the meteorites found in good condition from 2008 to 2010 (both inclusive).

In [ ]:
# Student Action: Find out how many meteorites found in good condition from 2008 to 2010 (both inclusive).
good_meteorites = found_valid_df[(found_valid_df['year'] >= 2008) & (found_valid_df['year'] <= 2010)]
good_meteorites

name     id nametype      recclass      mass   fall  year  \
1109     Abar al' Uj 001  51399    Valid          H3.8   194.340  Found  2008   
1589         Al Huqf 067  51921    Valid            H4    61.600  Found  2009   
1590         Al Huqf 068  51922    Valid            L3   165.400  Found  2009   
1591         Al Huqf 069  51923    Valid          H4/5   250.500  Found  2009   
1592         Al Huqf 070  51937    Valid            L4  2632.800  Found  2009   
...                  ...    ...      ...           ...       ...    ...   ...   
38320  Willcox Playa 009  52851    Valid  Mesosiderite   160.000  Found  2009   
38387         Yabrin 001  51008    Valid           LL5    65.190  Found  2008   
38388         Yabrin 002  51009    Valid            H5    46.320  Found  2008   
38389         Yabrin 003  48974    Valid   Acapulcoite    21.048  Found  2008   
45668    Yarle Lakes 004  52945    Valid           CK4     4.600  Found  2009   

         reclat    reclong               GeoLocation  
1109   22.72192   48.95937    (22.721920, 48.959370)  
1589   19.22597   57.54063    (19.225970, 57.540630)  
1590   19.14025   57.58427    (19.140250, 57.584270)  
1591   19.26795   57.13412    (19.267950, 57.134120)  
1592   19.18798   57.10978    (19.187980, 57.109780)  
...         ...        ...                       ...  
38320  32.07667 -109.84550  (32.076670, -109.845500)  
38387  23.34775   48.73742    (23.347750, 48.737420)  
38388  23.35717   48.72245    (23.357170, 48.722450)  
38389  23.31522   48.62988    (23.315220, 48.629880)  
45668 -30.50000  131.46667  (-30.500000, 131.466670)  

[976 rows x 10 columns]

So, 976 meteorites were found in good condition from 2008 to 2010 (both inclusive). Now, let's create a cartogram for these meteorites.

In [ ]:
# Student Action: Create a cartogram for the meteorites found in good condition from 2008 to 2010 (both inclusive).
map3 = folium.Map(location = [0,0], width = '90%', tiles = 'OpenStreetMap', zoom_start = 2)
for i in good_meteorites.index:
  folium.Marker(location = [good_meteorites.loc[i,'reclat'], good_meteorites.loc[i, 'reclong']], popup = good_meteorites.loc[i, 'name']).add_to(map3)

In [ ]:
map3

Similarly, let's create a cartogram for the meteorites found in good condition from 2005 to 2007 (both inclusive).

In [ ]:
# Student Action: How many meteorites were found in good condition from 2005 to 2007 (both inclusive)?
good_meteorites_2 = found_valid_df[(found_valid_df['year'] >= 2005) & (found_valid_df['year'] <= 2007)]
good_meteorites_2

name     id nametype        recclass        mass   fall  \
1514         Adam Talha  44856    Valid           LL3.2      259.30  Found   
1559         Al Alamayn  35484    Valid              H5       13.31  Found   
1560   Al Haggounia 001  44857    Valid         Aubrite  3000000.00  Found   
1585        Al Huqf 063  45832    Valid              L6      591.80  Found   
1587        Al Huqf 065  48537    Valid              L6     2084.16  Found   
...                 ...    ...      ...             ...         ...    ...   
38295        Whitecourt  47345    Valid     Iron, IIIAB     5372.00  Found   
38324       Willow Wash  47353    Valid            H3.5      552.00  Found   
45664     Yaringie Hill  48950    Valid              H5     5750.00  Found   
45674  Yelland Dry Lake  52641    Valid              H4    76000.00  Found   
45685             Youxi  55793    Valid  Mesosiderite-C   218000.00  Found   

       year     reclat    reclong               GeoLocation  
1514   2005  22.993500  -10.15367   (22.993500, -10.153670)  
1559   2005  30.709520   28.96980    (30.709520, 28.969800)  
1560   2006  27.500000  -12.50000   (27.500000, -12.500000)  
1585   2006  19.445330   57.02345    (19.445330, 57.023450)  
1587   2007  19.320920   57.22977    (19.320920, 57.229770)  
...     ...        ...        ...                       ...  
38295  2007  53.999167 -115.59750  (53.999167, -115.597500)  
38324  2006  35.373580 -115.34388  (35.373580, -115.343880)  
45664  2006 -32.082870  135.64985  (-32.082870, 135.649850)  
45674  2007  39.350670 -114.40783  (39.350670, -114.407830)  
45685  2006  26.060000  118.01000   (26.060000, 118.010000)  

[1688 rows x 10 columns]

So, 1688 meteorites were found in good condition from 2005 to 2007 (both inclusive). Now, let's create a cartogram for these meteorites.



In [ ]:
# Student Action: Create a cartogram for the meteorites found in good condition from 2005 to 2007 (both inclusive).
map4 = folium.Map(location = [0,0], width = '90%', tiles = 'OpenStreetMap', zoom_start = 2)
for i in good_meteorites_2.index:
  folium.Marker(location = [good_meteorites_2.loc[i,'reclat'], good_meteorites_2.loc[i, 'reclong']], popup = good_meteorites_2.loc[i, 'name']).add_to(map4)

In [ ]:
map4

The `popup` parameter displays the name of the location on a popup box when clicked on a marker. Along with the city name, we can also display the mass of a meteorite in the popup of the markers. For this, we will have to use **string concatenation**. It is a process in which two or more Python objects can be joined together into one string object.


In [ ]:
found_valid_df.head()

name     id nametype recclass      mass   fall  year  \
1108            Abajo      4    Valid       H5    331.00  Found  1982   
1109  Abar al' Uj 001  51399    Valid     H3.8    194.34  Found  2008   
1110           Abbott      5    Valid     H3-6  21100.00  Found  1951   
1111        Abernathy      7    Valid       L6   2914.00  Found  1941   
1112              Abo      8    Valid        H      1.20  Found  1840   

        reclat    reclong               GeoLocation  
1108  26.80000 -105.41667  (26.800000, -105.416670)  
1109  22.72192   48.95937    (22.721920, 48.959370)  
1110  36.30000 -104.28333  (36.300000, -104.283330)  
1111  33.85000 -101.80000  (33.850000, -101.800000)  
1112  60.43333   22.30000    (60.433330, 22.300000)

---

#### Activity 5: String Concatenation^^

Let's understand the string concatenation concept using a very simple example. Consider that we have two different information saved in the two different variables

1. `name = 'Bruce Wayne'`

2. `age = '30'`

Let's create the `'Hi! My name is Bruce Wayne and I am 30 years old.'` sentence using the two variables, then we can use string concatenation. To concatenate strings, you need to use the `+` operator.

**Note:** The code below will throw the `TypeError` error which is expected. So, don't worry about it.

In [ ]:
# Teacher Action: Create the 'Hi! My name is Bruce Wayne and I am 30 years old.' string using string concatenation method
# without converting the 'age' into an integer.
name = 'Rohan'
age = 17
name + age

TypeError: ignored

In [ ]:
name + str(age)

'Rohan17'

The above code throws an error because we are trying to concatenate an integer data type with a string data type. If a variable contains a non-string data type then you first have to convert it into a string using the `str()` function and then use the `+` operator to concatenate the strings.

In [ ]:
# Teacher Action: Create the 'Hi! My name is Bruce Wayne and I am 30 years old.' string using string concatenation method
# by converting the 'age' into an integer.


Similarly, we can concatenate each `name` value with the corresponding `mass` value and then display both the city names and the mass of a meteorite through the `popup` parameter. Let's display the name and the mass of the meteorites for the meteorites found in a condition from the year 2005 to 2007 (both inclusive).

In [ ]:
# Student Action: Use the string concatenation method to display the name of the place and mass of the meteorite in the marker popup.
map5 = folium.Map(location = [0,0], width = '90%', tiles = 'OpenStreetMap', zoom_start = 2)
for i in good_meteorites_2.index:
  folium.Marker(location = [good_meteorites_2.loc[i,'reclat'], good_meteorites_2.loc[i, 'reclong']], popup = good_meteorites_2.loc[i, 'name'] + " " + str(good_meteorites_2.loc[i, 'mass']) + " " + str(good_meteorites_2.loc[i, 'recclass'])).add_to(map5)

In [ ]:
map5

If you click on any of the markers, you will see that it displays both the city name and the mass of a meteorite. We can also add circular markers such that the radius of a circular marker represents the mass of the meteorite fallen. So, the bigger the circle, the heavier the meteorite.

In [ ]:
# Student Action: Add circular markers such that the radius of a circular marker represents the mass of the meteorite fallen.
map6 = folium.Map(location = [0,0], width = '90%', tiles = 'OpenStreetMap', zoom_start = 2)
for i in good_meteorites_2.index:
  folium.Circle(fill = True, fill_color = '#800080', radius = good_meteorites_2.loc[i, 'mass'], location = [good_meteorites_2.loc[i,'reclat'], good_meteorites_2.loc[i, 'reclong']], popup = good_meteorites_2.loc[i, 'name'] + " " + str(good_meteorites_2.loc[i, 'mass']) + " " + str(good_meteorites_2.loc[i, 'recclass'])).add_to(map6)

In [ ]:
map6

In your free time, you create cartograms for the remaining meteorites. In the next class, we will learn how to create the count plots.

**Note:** You can atttempt **Project 7** now.

---